# Coummunity Detection


Visualize the graph community for diverse time.

[weekdays]<br>
1. commuted time<br>
    6-10<br>
    16-21<br>
2. regular time(except commuted time)<br>
    10-16<br>
    
[weekends]<br>

3. time on weekends<br>
    6-10<br>
    10-16<br>
    16-21



In [27]:
import numpy as np
import pandas as pd
import pickle
import networkx as nx
import datetime as dt


import community as community_louvain

import folium
from folium import plugins
import matplotlib.cm as cm
import matplotlib.pyplot as plt


## Location EDA

- sensor location visualization
- community detection based on location

In [28]:
location = pd.read_csv('graph_sensor_locations_bay.csv',header = None)
location.columns=['sensor_id','latitude','longitude']
location

sensor_id   latitude   longitude
0       400001  37.364085 -121.901149
1       400017  37.253303 -121.945440
2       400030  37.359087 -121.906538
3       400040  37.294949 -121.873109
4       400045  37.363402 -121.902233
..         ...        ...         ...
320     413845  37.422887 -121.925747
321     413877  37.321613 -121.899642
322     413878  37.324641 -121.888603
323     414284  37.323066 -121.896538
324     414694  37.315051 -121.913497

[325 rows x 3 columns]

In [29]:
map_osm = folium.Map(location=[37.364085,-121.901149], zoom_start=12)


for i in location.index:
    # 행 우선 접근 방식으로 값 추출하기
    name = location.loc[i, 'sensor_id']
    lat = location.loc[i, 'latitude']
    lng = location.loc[i, 'longitude']
    
    # 추출한 정보를 지도에 표시
    marker = folium.Marker([lat,lng], popup=name, icon=folium.Icon(color='blue'))
    marker.add_to(map_osm)

map_osm

In [30]:
### Read adj_matrix (DCRNN>data)
with open('./adj_mx_bay.pkl', 'rb') as f:
    u = pickle._Unpickler(f)
    u.encoding = 'latin1'
    adj_bay = u.load()
adj_bay = np.array(adj_bay)[-1]
adj_bay

G = nx.Graph(adj_bay)
# compute the best partition
partition = community_louvain.best_partition(G)

'''
# draw the graph
pos = nx.spring_layout(G)
# color the nodes according to their partition
cmap = cm.get_cmap('viridis', max(partition.values()) + 1)
nx.draw_networkx_nodes(G, pos, partition.keys(), node_size=40,
                       cmap=cmap, node_color=list(partition.values()))
nx.draw_networkx_edges(G, pos, alpha=0.5)
plt.show()
'''


set(partition.values()) ## 25 communities

{0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22}

In [31]:
#colors = ['orange', 'blue', 'lightblue', 'lightred', 'beige', 'darkred', 'lightgreen', 'darkblue', 'black', 'darkgreen', 'pink', 'cadetblue', 'white', 'green', 'gray', 'darkpurple', 'purple', 'lightgray', 'red']
#len(colors)
colors = ['#130306', '#FFF4F6', '#FFAA00', '#7D6C81', '#288E7F', '#CFE600', '#DED4DD', '#E105A2', '#E10529', '#FF190E', '#FF700E','#69310B', '#FEF250', '#8DF525', '#0DEA71', '#136A68', '#3F7BE8', '#493DDE', '#BF3DDE', '#450454' '#FF5733', '#C29E1B', '#FFEDAB', '#4B601B', '#04FEBD', '#849AEB', '#F2D3FF']

### Community detection based on distance

It it the result of community detection by distance based adjacency matrix.<br>
The communities are seperated depend on intersection, because in the data, there is not distance between sensors beyond intersection.

In [32]:


map_osm = folium.Map(location=[37.364085,-121.901149], zoom_start=17)


for i in location.index:
    # 행 우선 접근 방식으로 값 추출하기
    name = location.loc[i, 'sensor_id']
    lat = location.loc[i, 'latitude']
    lng = location.loc[i, 'longitude']
    c = partition[i]
    # 추출한 정보를 지도에 표시 # coummunity 25개 찾았는데 색은 19개 뿐...ㅋㅋ
    if c <= 18:
        marker = folium.Marker([lat,lng], popup=name, icon=plugins.BeautifyIcon(border_width=6 ,icon_shape = 'doughnut', border_color=colors[c]))
        marker.add_to(map_osm)


map_osm

## Comumunity detection by Speed

In [33]:
'''
### Read speed data to do prediction task
speed_bay = pd.read_hdf('./pems-bay.h5')
speed_bay

'''


"\n### Read speed data to do prediction task\nspeed_bay = pd.read_hdf('./pems-bay.h5')\nspeed_bay\n\n"

In [34]:

speed_bay = pd.read_csv("bay.csv")
speed_bay

Unnamed: 0  400001  400017  400030  400040  400045  400052  \
0      2017-01-01 00:00:00    71.4    67.8    70.5    67.4    68.8    66.6   
1      2017-01-01 00:05:00    71.6    67.5    70.6    67.5    68.7    66.6   
2      2017-01-01 00:10:00    71.6    67.6    70.2    67.4    68.7    66.1   
3      2017-01-01 00:15:00    71.1    67.5    70.3    68.0    68.5    66.7   
4      2017-01-01 00:20:00    71.7    67.8    70.2    68.1    68.4    66.9   
...                    ...     ...     ...     ...     ...     ...     ...   
52111  2017-06-30 23:35:00    70.9    66.3    68.4    61.0    61.8    66.9   
52112  2017-06-30 23:40:00    71.3    66.6    68.7    60.9    62.0    66.2   
52113  2017-06-30 23:45:00    71.4    66.9    68.1    61.1    62.0    66.7   
52114  2017-06-30 23:50:00    72.2    66.5    68.0    61.1    62.5    65.8   
52115  2017-06-30 23:55:00    71.5    66.2    68.4    61.5    62.8    66.1   

       400057  400059  400065  ...  409525  409526  409528  409529  413026  \
0        66.8    68.0    66.8  ...    68.8    67.9    68.8    68.0    69.2   
1        66.8    67.8    66.5  ...    68.4    67.3    68.4    67.6    70.4   
2        66.8    67.8    66.2  ...    68.4    67.4    68.4    67.5    70.2   
3        66.6    67.7    65.9  ...    68.5    67.5    68.5    67.5    70.4   
4        66.1    67.7    66.1  ...    68.5    67.7    68.5    67.4    69.6   
...       ...     ...     ...  ...     ...     ...     ...     ...     ...   
52111    66.0    67.4    65.4  ...    64.6    66.8    64.7    61.1    68.4   
52112    66.5    68.2    64.9  ...    65.1    67.3    64.8    60.8    69.8   
52113    65.8    68.2    64.2  ...    64.9    66.5    64.6    61.3    69.5   
52114    67.1    68.3    64.0  ...    64.1    65.9    64.8    61.3    69.6   
52115    67.7    68.4    64.9  ...    64.3    66.5    64.8    60.9    70.9   

       413845  413877  413878  414284  414694  
0        68.9    70.4    68.8    71.1    68.0  
1        68.8    70.1    68.4    70.8    67.4  
2        68.3    69.8    68.4    70.5    67.9  
3        68.7    70.2    68.4    70.8    67.6  
4        69.1    70.0    68.4    71.0    67.9  
...       ...     ...     ...     ...     ...  
52111    61.4    70.5    68.2    71.6    66.2  
52112    62.2    69.4    68.6    71.6    68.4  
52113    63.8    70.6    68.4    71.6    66.6  
52114    64.2    70.2    68.7    71.6    68.4  
52115    63.4    70.3    68.7    71.6    68.0  

[52116 rows x 326 columns]

### add day_name

In [9]:
speed_bay['Unnamed: 0'] = pd.to_datetime(speed_bay['Unnamed: 0'])
speed_bay['w_name'] = speed_bay['Unnamed: 0'].dt.day_name()
speed_bay.head()

Unnamed: 0  400001  400017  400030  400040  400045  400052  400057  \
0 2017-01-01 00:00:00    71.4    67.8    70.5    67.4    68.8    66.6    66.8   
1 2017-01-01 00:05:00    71.6    67.5    70.6    67.5    68.7    66.6    66.8   
2 2017-01-01 00:10:00    71.6    67.6    70.2    67.4    68.7    66.1    66.8   
3 2017-01-01 00:15:00    71.1    67.5    70.3    68.0    68.5    66.7    66.6   
4 2017-01-01 00:20:00    71.7    67.8    70.2    68.1    68.4    66.9    66.1   

   400059  400065  ...  409526  409528  409529  413026  413845  413877  \
0    68.0    66.8  ...    67.9    68.8    68.0    69.2    68.9    70.4   
1    67.8    66.5  ...    67.3    68.4    67.6    70.4    68.8    70.1   
2    67.8    66.2  ...    67.4    68.4    67.5    70.2    68.3    69.8   
3    67.7    65.9  ...    67.5    68.5    67.5    70.4    68.7    70.2   
4    67.7    66.1  ...    67.7    68.5    67.4    69.6    69.1    70.0   

   413878  414284  414694  w_name  
0    68.8    71.1    68.0  Sunday  
1    68.4    70.8    67.4  Sunday  
2    68.4    70.5    67.9  Sunday  
3    68.4    70.8    67.6  Sunday  
4    68.4    71.0    67.9  Sunday  

[5 rows x 327 columns]

### seperate data by time

6-10,10-16,16-21

In [10]:
date_time = list(speed_bay['Unnamed: 0'])

In [11]:
six_to_10 = []
ten_to_16 =[]
sixteens_to_21 = []

for i in range(len(date_time)):
    if date_time[i].hour in range(6,10):
        six_to_10.append(speed_bay.iloc[i])
        
    elif speed_bay['Unnamed: 0'][i].hour in range(10,16):
        ten_to_16.append(speed_bay.iloc[i])
        
    elif speed_bay['Unnamed: 0'][i].hour in range(16,21):
        sixteens_to_21.append(speed_bay.iloc[i])
        
        
six_to_10 = pd.DataFrame(six_to_10)
ten_to_16 = pd.DataFrame(ten_to_16)
sixteens_to_21 = pd.DataFrame(sixteens_to_21)

### weekdays and weekends

In [12]:
six_to_10_S = six_to_10[(six_to_10['w_name'] == 'Sunday')| (six_to_10['w_name'] == 'Saturday')]
six_to_10_W = six_to_10[(six_to_10['w_name']!= 'Sunday') & (six_to_10['w_name'] != 'Saturday')]


ten_to_16_S = ten_to_16[(ten_to_16['w_name'] == 'Sunday')| (ten_to_16['w_name'] == 'Saturday')]
ten_to_16_W = ten_to_16[(ten_to_16['w_name']!= 'Sunday') & (ten_to_16['w_name'] != 'Saturday')]

sixteens_to_21_S = sixteens_to_21[(sixteens_to_21['w_name'] == 'Sunday')| (sixteens_to_21['w_name'] == 'Saturday')]
sixteens_to_21_W = sixteens_to_21[(sixteens_to_21['w_name']!= 'Sunday') & (sixteens_to_21['w_name'] != 'Saturday')]


In [13]:
six_to_10_W

Unnamed: 0  400001  400017  400030  400040  400045  400052  \
360   2017-01-02 06:00:00    67.0    68.2    68.6    67.1    67.9    65.9   
361   2017-01-02 06:05:00    64.9    67.7    68.1    68.2    67.1    64.8   
362   2017-01-02 06:10:00    64.9    67.8    67.4    67.7    66.7    62.6   
363   2017-01-02 06:15:00    64.7    67.6    67.5    67.8    66.5    61.3   
364   2017-01-02 06:20:00    64.1    67.4    67.4    67.5    66.2    58.6   
...                   ...     ...     ...     ...     ...     ...     ...   
51943 2017-06-30 09:35:00    62.7    64.9    59.0    55.5    35.8    63.0   
51944 2017-06-30 09:40:00    63.2    65.3    58.2    55.7    37.7    64.1   
51945 2017-06-30 09:45:00    62.0    65.5    56.5    56.3    47.6    65.0   
51946 2017-06-30 09:50:00    61.4    64.9    56.9    55.0    52.0    64.5   
51947 2017-06-30 09:55:00    61.9    64.9    58.8    56.6    53.7    64.5   

       400057  400059  400065  ...  409526  409528  409529  413026  413845  \
360      68.4    67.3    65.0  ...    64.6    67.8    66.6    68.2    55.9   
361      67.0    66.9    65.7  ...    66.2    67.1    66.1    67.8    63.5   
362      67.1    66.5    65.9  ...    66.9    66.8    65.7    66.5    65.3   
363      66.7    66.4    65.6  ...    66.3    66.6    65.4    66.5    66.7   
364      65.2    66.4    64.7  ...    66.1    66.4    65.3    66.3    65.7   
...       ...     ...     ...  ...     ...     ...     ...     ...     ...   
51943    53.0    66.7    58.4  ...    62.7    59.7    56.2    62.4    30.8   
51944    57.5    66.2    60.4  ...    61.9    59.7    56.5    63.1    32.7   
51945    59.4    64.5    61.7  ...    63.1    59.9    56.4    62.5    31.5   
51946    58.1    66.4    61.5  ...    64.2    60.2    57.2    62.0    31.1   
51947    59.6    66.1    62.6  ...    63.9    59.4    55.3    62.1    30.3   

       413877  413878  414284  414694  w_name  
360      71.7    67.7    70.0    67.1  Monday  
361      71.8    67.0    68.9    67.0  Monday  
362      71.1    66.7    68.2    65.7  Monday  
363      69.9    66.5    68.0    64.2  Monday  
364      69.8    66.3    66.3    63.5  Monday  
...       ...     ...     ...     ...     ...  
51943    72.1    62.6    67.5    61.3  Friday  
51944    74.2    61.5    67.4    61.4  Friday  
51945    74.3    62.1    67.6    62.9  Friday  
51946    72.9    62.4    67.5    63.8  Friday  
51947    74.4    62.9    67.8    64.0  Friday  

[6240 rows x 327 columns]

### make adjacent matrix

- for mean of sensor's speed
- by using gaussian kernels

In [14]:
def Gaussian(x,z,sigma):
    return np.exp((-(np.linalg.norm(x-z)**2))/(2*sigma**2))

def GaussianMatrix(X,sigma):
    row,col=X.shape
    GassMatrix=np.zeros(shape=(row,row))
    X=np.asarray(X)
    i=0
    for v_i in X:
        j=0
        for v_j in X:
            GassMatrix[i,j]=Gaussian(v_i.T,v_j.T,sigma)
            j+=1
        i+=1
    return GassMatrix

def adj_mat_speed(data):
    mean = pd.DataFrame(data.mean(axis = 0))
    adj_mat = GaussianMatrix(mean,sigma = 1)
    
    return adj_mat

In [15]:
def visualization_community(data,location):
    
    G = nx.Graph(adj_mat_speed(data))
    # compute the best partition
    partition = community_louvain.best_partition(G)
    
    stat = pd.DataFrame(data.mean(axis = 0),columns = ['AvgSpeed'])
    stat['community'] = partition.values()
    report = stat.groupby(stat['community']).describe()
    report.index = colors[:len(report)]
    print(report)
    
    
    map_osm = folium.Map(location=[37.364085,-121.901149], zoom_start=12)

    for i in location.index:
        # 행 우선 접근 방식으로 값 추출하기
        name = location.loc[i, 'sensor_id']
        lat = location.loc[i, 'latitude']
        lng = location.loc[i, 'longitude']
        c = partition[i]
        
        # can visualize 18th community.(because of limiation of Marker)
        if c <= 18:
            marker = folium.Marker([lat,lng], popup=name, icon=folium.Icon(color=colors[c]))
            marker.add_to(map_osm)

    return map_osm

### 6-10 weekdays

<strong>[The lowest speed & intersection]</strong><br>
The lowest speed sensor community for each map is existed in intersection.<br>
In 6-10 weekdays map, the darkred simbols show that the sensors have the slowest speed(mean of speed in the community:34). They usually are in intersection.<br>
We can also check the beige simbol in 16-21 weekdays map which has the lowest speed(mean of speed in the community:29), and they are also in intersection.<br>
However, the 10-16 weekdays map has the lowest mean of speed in the community as 46 at the intersection.<br>

Therefore, we can concluded that the intersections are more crowed in commuted time(6-10(dark red),16-21(beige)) than regular time.


<strong>[For west valley free way ]</strong><br>
In 6-10 weekdays map, the down line of west valley free way is concured by blue community(mean of speed: 65), while the up line of west valley free way is most concured by light blue and orange community(mean of speed: 43,51). It means that the down line of the road is less blocked than the up line.<br>
In 16-21 weekdays map, the down line of west valley free way is concured by blue community(mean of speed: 42), while the up line of west valley free way is most concured by light red and orange community(mean of speed: 59,66). It means that the up line of the road is less blocked than the down line.<br>

Since the direction of the fast-speed road between going to work hour and leaving the office hour has changed, it would be seems many office are concentrated at the end of the upward line of this road.


In [35]:
colors = ['orange', 'blue', 'lightblue', 'lightred', 'beige', 'darkred', 'lightgreen', 'darkblue', 'black', 'darkgreen', 'pink', 'cadetblue', 'white', 'green', 'gray', 'darkpurple', 'purple', 'lightgray', 'red']

In [36]:
visualization_community(six_to_10_W,location)

<ipython-input-14-e222ea16b736>:18: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  mean = pd.DataFrame(data.mean(axis = 0))
<ipython-input-15-cea93cbe2131>:7: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  stat = pd.DataFrame(data.mean(axis = 0),columns = ['AvgSpeed'])


          AvgSpeed                                                        \
             count       mean       std        min        25%        50%   
orange        44.0  51.945629  1.830737  48.252660  50.424251  52.099231   
blue          95.0  65.442404  1.308366  63.764615  64.466066  65.125112   
lightblue     50.0  43.554488  2.417657  38.995288  41.580040  43.507364   
lightred      51.0  62.530646  0.615508  61.420529  62.109511  62.519663   
beige         68.0  58.676992  1.634135  55.483141  57.623337  58.678670   
darkred       17.0  34.381105  2.781774  29.460321  32.413718  34.656394   

                                 
                 75%        max  
orange     53.157019  54.944679  
blue       65.986138  69.678654  
lightblue  45.853862  47.790801  
lightred   63.034191  63.665176  
beige      60.069523  61.147981  
darkred    36.708894  37.883846  


### 6-10 weekends

In [37]:
visualization_community(six_to_10_S,location)

<ipython-input-14-e222ea16b736>:18: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  mean = pd.DataFrame(data.mean(axis = 0))
<ipython-input-15-cea93cbe2131>:7: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  stat = pd.DataFrame(data.mean(axis = 0),columns = ['AvgSpeed'])


          AvgSpeed                                                        \
             count       mean       std        min        25%        50%   
orange       126.0  68.178034  0.984428  67.064992  67.442085  67.922569   
blue          93.0  64.090506  1.175328  60.138235  63.421528  64.406985   
lightblue    102.0  66.389804  0.401988  65.632843  66.072937  66.413113   
lightred       1.0  49.420874       NaN  49.420874  49.420874  49.420874   
beige          3.0  58.813045  0.523310  58.419240  58.516136  58.613031   

                                 
                 75%        max  
orange     68.505341  71.556413  
blue       64.880882  65.561438  
lightblue  66.732190  67.039828  
lightred   49.420874  49.420874  
beige      59.009947  59.406863  


### 6-10 all days

In [38]:
visualization_community(six_to_10,location)

<ipython-input-14-e222ea16b736>:18: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  mean = pd.DataFrame(data.mean(axis = 0))
<ipython-input-15-cea93cbe2131>:7: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  stat = pd.DataFrame(data.mean(axis = 0),columns = ['AvgSpeed'])


          AvgSpeed                                                        \
             count       mean       std        min        25%        50%   
orange        43.0  56.430829  1.274290  53.957585  55.604414  56.249712   
blue         100.0  65.910328  1.214617  64.426047  65.052573  65.613455   
lightblue     61.0  49.722879  2.294830  44.628626  48.174632  49.804132   
lightred      54.0  63.273537  0.614358  62.128764  62.931526  63.239129   
beige         56.0  60.543980  0.987137  58.718750  59.736018  60.445246   
darkred       11.0  41.891575  1.568642  39.016897  40.968710  41.972376   

                                 
                 75%        max  
orange     57.432366  58.408840  
blue       66.431759  70.207746  
lightblue  51.651001  53.685820  
lightred   63.642941  64.308253  
beige      61.367792  61.992116  
darkred    43.291229  43.831181  


In [39]:
six_to_10_S = six_to_10[(six_to_10['w_name'] == 'Sunday')| (six_to_10['w_name'] == 'Saturday')]
six_to_10_W = six_to_10[(six_to_10['w_name']!= 'Sunday') & (six_to_10['w_name'] != 'Saturday')]


ten_to_16_S = ten_to_16[(ten_to_16['w_name'] == 'Sunday')| (ten_to_16['w_name'] == 'Saturday')]
ten_to_16_W = ten_to_16[(ten_to_16['w_name']!= 'Sunday') & (ten_to_16['w_name'] != 'Saturday')]

sixteens_to_21_S = sixteens_to_21[(sixteens_to_21['w_name'] == 'Sunday')| (sixteens_to_21['w_name'] == 'Saturday')]
sixteens_to_21_W = sixteens_to_21[(sixteens_to_21['w_name']!= 'Sunday') & (sixteens_to_21['w_name'] != 'Saturday')]


### 10-16 weekdays

In [40]:
visualization_community(ten_to_16_W,location)

<ipython-input-14-e222ea16b736>:18: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  mean = pd.DataFrame(data.mean(axis = 0))
<ipython-input-15-cea93cbe2131>:7: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  stat = pd.DataFrame(data.mean(axis = 0),columns = ['AvgSpeed'])


          AvgSpeed                                                        \
             count       mean       std        min        25%        50%   
orange       114.0  64.656890  1.272961  62.889167  63.621944  64.342345   
blue         118.0  57.743034  1.983988  50.955481  56.747481  58.050726   
lightblue     87.0  61.740256  0.630661  60.518301  61.287682  61.746496   
lightred       6.0  46.266766  1.515718  44.218045  45.520649  45.949386   

                                 
                 75%        max  
orange     65.622356  68.418547  
blue       59.270467  60.377853  
lightblue  62.254605  62.766987  
lightred   47.397561  48.225759  


### 10-16 weekends

In [41]:
visualization_community(ten_to_16_S,location)

<ipython-input-14-e222ea16b736>:18: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  mean = pd.DataFrame(data.mean(axis = 0))
<ipython-input-15-cea93cbe2131>:7: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  stat = pd.DataFrame(data.mean(axis = 0),columns = ['AvgSpeed'])


          AvgSpeed                                                        \
             count       mean       std        min        25%        50%   
orange       105.0  67.066516  0.951218  65.769009  66.402260  66.720261   
blue         105.0  61.916229  1.283054  58.818764  61.028023  62.222249   
lightblue     22.0  55.876432  2.097826  51.494935  54.380855  56.165591   
lightred      90.0  64.813380  0.543951  63.783415  64.366006  64.828568   
beige          3.0  46.307925  1.814117  44.761029  45.309572  45.858115   

                                 
                 75%        max  
orange     67.638426  69.890005  
blue       62.936819  63.753622  
lightblue  57.644513  58.365414  
lightred   65.266136  65.715441  
beige      47.081373  48.304630  


### 10-16 all days

In [42]:
visualization_community(ten_to_16,location)

<ipython-input-14-e222ea16b736>:18: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  mean = pd.DataFrame(data.mean(axis = 0))
<ipython-input-15-cea93cbe2131>:7: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  stat = pd.DataFrame(data.mean(axis = 0),columns = ['AvgSpeed'])


          AvgSpeed                                                        \
             count       mean       std        min        25%        50%   
orange       127.0  64.960872  1.239366  63.177425  63.961971  64.659431   
blue         102.0  58.677459  1.498711  54.745450  57.726349  58.884074   
lightblue     86.0  62.143675  0.563084  60.918470  61.779815  62.173170   
lightred      10.0  51.077822  1.676865  47.659423  50.008961  51.763191   

                                 
                 75%        max  
orange     65.743462  68.704497  
blue       59.878158  60.801796  
lightblue  62.600787  63.144690  
lightred   52.280485  52.824747  


### 16-21 weekdays

In [43]:
visualization_community(sixteens_to_21_W,location)

<ipython-input-14-e222ea16b736>:18: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  mean = pd.DataFrame(data.mean(axis = 0))
<ipython-input-15-cea93cbe2131>:7: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  stat = pd.DataFrame(data.mean(axis = 0),columns = ['AvgSpeed'])


          AvgSpeed                                                        \
             count       mean       std        min        25%        50%   
orange        71.0  66.712568  1.187385  65.244000  65.870250  66.342590   
blue          63.0  42.327963  3.384588  33.778590  40.212212  42.925321   
lightblue     60.0  51.975768  2.142147  47.676167  50.325619  51.865269   
lightred      36.0  58.236469  1.336221  55.838872  56.983641  58.222071   
beige          4.0  29.611564  1.657117  27.617987  28.704872  29.668340   
darkred       91.0  63.288696  1.246488  60.687731  62.343147  63.551679   

                                 
                 75%        max  
orange     67.364378  70.717000  
blue       45.058359  47.139564  
lightblue  53.878718  55.525667  
lightred   59.450990  60.219872  
beige      30.575032  31.491590  
darkred    64.222955  65.166167  


### 16-21 weekends

In [44]:
visualization_community(sixteens_to_21_S,location)

<ipython-input-14-e222ea16b736>:18: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  mean = pd.DataFrame(data.mean(axis = 0))
<ipython-input-15-cea93cbe2131>:7: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  stat = pd.DataFrame(data.mean(axis = 0),columns = ['AvgSpeed'])


          AvgSpeed                                                        \
             count       mean       std        min        25%        50%   
orange       114.0  67.428039  1.016781  66.146373  66.617712  67.157484   
blue          92.0  64.152442  0.578153  62.954608  63.705980  64.257418   
lightblue     62.0  60.771843  1.628452  56.200588  60.013570  61.114542   
lightred      47.0  65.617008  0.254630  65.139412  65.417418  65.656569   
beige         10.0  52.273908  2.491310  47.762353  50.512941  52.515915   

                                 
                 75%        max  
orange     67.929959  70.818824  
blue       64.687721  65.059052  
lightblue  62.066577  62.717549  
lightred   65.786422  66.101144  
beige      54.330359  55.450458  


### 16-21 all days

In [45]:
visualization_community(sixteens_to_21,location)

<ipython-input-14-e222ea16b736>:18: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  mean = pd.DataFrame(data.mean(axis = 0))
<ipython-input-15-cea93cbe2131>:7: FutureWarning: DataFrame.mean and DataFrame.median with numeric_only=None will include datetime64 and datetime64tz columns in a future version.
  stat = pd.DataFrame(data.mean(axis = 0),columns = ['AvgSpeed'])


          AvgSpeed                                                        \
             count       mean       std        min        25%        50%   
orange        77.0  66.742422  1.165062  65.174899  65.737523  66.475028   
blue          61.0  47.973978  2.686039  41.003702  46.533158  48.155755   
lightblue     59.0  54.840759  1.518972  52.043536  53.599240  54.726501   
lightred      43.0  59.525488  0.945702  57.808545  58.846459  59.721906   
beige         82.0  63.592140  0.964893  61.634521  62.942109  63.822477   
darkred        3.0  38.641562  0.811648  37.738011  38.307891  38.877772   

                                 
                 75%        max  
orange     67.284116  70.513462  
blue       50.091142  51.810258  
lightblue  56.124503  57.536529  
lightred   60.283158  61.109116  
beige      64.346593  65.073094  
darkred    39.093338  39.308904  
